In [5]:
import cv2
import mediapipe as mp

# MediaPipe Hands 모듈 초기화
mp_hands = mp.solutions.hands
hands = mp_hands.Hands(
    max_num_hands=2,               # 동시에 추적할 최대 손의 수
    min_detection_confidence=0.5,  # 손 검출을 위한 최소 신뢰도
    min_tracking_confidence=0.5)   # 손 추적을 위한 최소 신뢰도
mp_drawing = mp.solutions.drawing_utils  # 그리기 함수 초기화

# 웹캠 설정
cap = cv2.VideoCapture(0)

while cap.isOpened():
    success, image = cap.read()
    if not success:
        continue

    # BGR 이미지를 RGB로 변환
    image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)

    # 이미지 반전
    image = cv2.flip(image, 1)

    # 성능을 위해 이미지 쓰기 불가능으로 설정
    # MediaPipe를 통해 손 검출
    results = hands.process(image)

    # 이미지를 RGB에서 BGR로 변환하여 그리기 작업 준비
    image = cv2.cvtColor(image, cv2.COLOR_RGB2BGR)

    # 검출된 손의 랜드마크를 이미지에 그림 및 위치 저장
    hand_landmarks_list = []
    if results.multi_hand_landmarks:
        for hand_landmarks in results.multi_hand_landmarks:
            # 랜드마크 그리기
            mp_drawing.draw_landmarks(
                image, hand_landmarks, mp_hands.HAND_CONNECTIONS,
                mp_drawing.DrawingSpec(color=(121, 22, 76), thickness=2, circle_radius=4),
                mp_drawing.DrawingSpec(color=(250, 44, 250), thickness=2))
            # 손의 위치 저장
            hand_landmarks_list.append(hand_landmarks)
            print(hand_landmarks_list)

    # 결과 이미지 표시
    cv2.imshow('Hand Tracking', image)

    # 손의 위치 변수에 저장
    # 여기서 hand_landmarks_list를 사용하여 원하는 위치에 접근하여 변수에 저장할 수 있습니다.
    # 예를 들어 첫 번째 손의 위치를 저장하려면 hand_landmarks_list[0]를 사용할 수 있습니다.

    # 'q'를 눌러 종료
    if cv2.waitKey(5) & 0xFF == ord('q'):
        break

cap.release()
cv2.destroyAllWindows()




[landmark {
  x: 0.982487142086029
  y: 0.7736784815788269
  z: 2.585198046745063e-07
}
landmark {
  x: 0.9427217841148376
  y: 0.7444488406181335
  z: -0.0939456969499588
}
landmark {
  x: 0.9162974953651428
  y: 0.6591793894767761
  z: -0.11080759763717651
}
landmark {
  x: 0.9044204950332642
  y: 0.5865879058837891
  z: -0.10077796131372452
}
landmark {
  x: 0.9088351726531982
  y: 0.5105350017547607
  z: -0.08294205367565155
}
landmark {
  x: 0.9659916758537292
  y: 0.5302546620368958
  z: -0.07635882496833801
}
landmark {
  x: 0.9617899060249329
  y: 0.4143103361129761
  z: -0.09335757791996002
}
landmark {
  x: 0.9645791053771973
  y: 0.33243948221206665
  z: -0.10729163140058517
}
landmark {
  x: 0.971206784248352
  y: 0.26888084411621094
  z: -0.11399777978658676
}
landmark {
  x: 0.9640694856643677
  y: 0.546279788017273
  z: -0.01960255578160286
}
landmark {
  x: 0.9531030654907227
  y: 0.47278428077697754
  z: -0.02174253575503826
}
landmark {
  x: 0.9558136463165283
  y: 0.

In [5]:
import mediapipe as mp
import cv2
import socket

# TCP 서버 설정
def send_hand_position(host='127.0.0.1', port=6521):
    # 소켓 객체 생성
    with socket.socket(socket.AF_INET, socket.SOCK_STREAM) as client_socket:
        # 서버에 연결
        client_socket.connect((host, port))
        print(f"서버에 연결되었습니다. {host}:{port}")

        # MediaPipe Hands 설정
        hands = mp.solutions.hands.Hands(
            min_detection_confidence=0.5,
            min_tracking_confidence=0.5)

        # 웹캠 캡처
        cap = cv2.VideoCapture(0)

        while True:
            # 이미지 읽기
            ret, image = cap.read()
            if not ret:
                break

            # 이미지 변환
            image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)

            # 손 검출
            results = hands.process(image)

            # 손 위치 정보 확인
            if results.multi_hand_landmarks:
                for hand_landmarks in results.multi_hand_landmarks:
                    # 손의 위치를 소켓으로 전송
                    hand_position = hand_landmarks.landmark[0]  # 첫 번째 랜드마크는 손목
                    hand_position_str = f"{hand_position.x},{hand_position.y},{hand_position.z}"
                    print(hand_position_str)
                    client_socket.sendall(hand_position_str.encode())

            # 이미지 출력
            image = cv2.cvtColor(image, cv2.COLOR_RGB2BGR)
            cv2.imshow('Hand Tracking', image)

            # 키 입력 처리
            if cv2.waitKey(5) & 0xFF == ord('q'):
                break

        # 자원 해제
        cap.release()
        cv2.destroyAllWindows()

if __name__ == "__main__":
    send_hand_position()

서버에 연결되었습니다. 127.0.0.1:6521
0.049293555319309235,0.9935992360115051,4.3998198862027493e-07
0.07357658445835114,0.9415283203125,7.47720207527891e-07
0.09538226574659348,0.8789018392562866,8.044044648158888e-07
0.11627799272537231,0.8080086708068848,7.818586027497076e-07
0.13757623732089996,0.7433680295944214,7.606123517689412e-07
0.15242691338062286,0.7233835458755493,7.376478379228502e-07
0.1493844985961914,0.7270431518554688,6.574351800736622e-07
0.18798404932022095,0.7535613775253296,6.507760303975374e-07
0.1855003833770752,0.7644254565238953,6.66952985284297e-07
0.17973554134368896,0.764255940914154,6.970920480853238e-07
0.1710619032382965,0.7590333819389343,7.193417559392401e-07
0.16415369510650635,0.7511656284332275,7.254897127495497e-07
0.15858232975006104,0.7462631464004517,7.183761567830516e-07
0.15695428848266602,0.7422921657562256,7.107940973583027e-07
0.15700337290763855,0.7404826879501343,7.075184953464486e-07
0.15622207522392273,0.7393822073936462,7.179266958701191e-07
0.1

In [6]:
import mediapipe as mp
import cv2

# MediaPipe Pose 설정
pose = mp.solutions.pose.Pose(
    static_image_mode=False, # 입력 이미지가 정적 이미지인지, 비디오 스트림 프레임인지 설정(False인 경우 비디오 스트림으로 처리)
    model_complexity=1, # 0,1,2 의 순으로 정확도가 올라가는 대신 속도가 느림
    smooth_landmarks=True, # 프레임간의 랜드 마크 위치를 부드럽게 처리할 지 여부 결정
    enable_segmentation=True, # 포즈 검출과 인물 마스크를 생성할지 여부 결정. 배경 제거 등의 용도로 사용
    smooth_segmentation=True, # 인물 마스크의 경계를 부드럽게 처리
    min_detection_confidence=0.5, # 사람 검출 최소 신뢰도 임계값
    min_tracking_confidence=0.5 # 포즈 추적의 신뢰도 임계값
)

# 그리기 함수 초기화
mp_drawing = mp.solutions.drawing_utils

# 웹캠 캡처
cap = cv2.VideoCapture(0)

while True:
    # 이미지 읽기
    ret, image = cap.read()
    if not ret:
        break

    # 이미지 변환
    image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)

    # 포즈 추정
    results = pose.process(image)

    # 추정된 포즈 정보 확인
    if results.pose_landmarks:

        # 연결된 랜드마크 시각화
        mp_drawing.draw_landmarks(
            image, results.pose_landmarks, mp.solutions.pose.POSE_CONNECTIONS)

    # 세그멘테이션 마스크 추출 및 배경 제거
    image = cv2.cvtColor(image, cv2.COLOR_RGB2BGR)

    if results.segmentation_mask is not None:
        # 세그멘테이션 마스크를 이미지 크기에 맞게 조정
        segmentation_mask = results.segmentation_mask
        segmentation_mask = (segmentation_mask > 0.1)  # 임계값 적용
        segmentation_mask = segmentation_mask.astype(float)
        
        # 세그멘테이션 마스크를 3채널로 복제하여 컬러 이미지와 동일한 차원으로 만듦
        mask_three_channel = cv2.merge([segmentation_mask, segmentation_mask, segmentation_mask])
        
        # 마스크를 적용하여 배경을 제거한 이미지 생성
        foreground = cv2.multiply(mask_three_channel, image.astype(float))
        
        cv2.imshow('Foreground', foreground.astype('uint8'))

    # 이미지 출력
    cv2.imshow('MediaPipe Pose', image)

    # 키 입력 처리
    if cv2.waitKey(5) & 0xFF == ord('q'):
        break

cap.release()
cv2.destroyAllWindows()

##### 포즈 landmarks 좌표 소켓 서버 전송

In [13]:
import mediapipe as mp
import cv2
import socket

# TCP 서버 설정
def send_pose_landmarks(host='127.0.0.1', port=6521):
    # 소켓 객체 생성
    with socket.socket(socket.AF_INET, socket.SOCK_STREAM) as client_socket:
        # 서버에 연결
        client_socket.connect((host, port))
        print(f"서버에 연결되었습니다. {host}:{port}")

        # MediaPipe Pose 설정
        pose = mp.solutions.pose.Pose(
            static_image_mode=False,
            model_complexity=1,
            smooth_landmarks=True,
            enable_segmentation=False,  # 세그멘테이션 기능 비활성화
            min_detection_confidence=0.5,
            min_tracking_confidence=0.5)

        # 그리기 함수 초기화
        mp_drawing = mp.solutions.drawing_utils

        # 웹캠 캡처
        cap = cv2.VideoCapture(0)

        while True:
            # 이미지 읽기
            ret, image = cap.read()
            if not ret:
                break

            # 이미지 변환
            image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)

            # 포즈 추정
            results = pose.process(image)

            # 추정된 포즈 정보 확인
            if results.pose_landmarks:
                # 포즈 랜드마크를 리스트로 변환하여 문자열로 만듦
                pose_landmarks_str = ';'.join(
                    [f"{lm.x},{lm.y},{lm.z}" for lm in results.pose_landmarks.landmark])

                # 포즈 랜드마크 문자열 출력
                print(pose_landmarks_str)

                # 포즈 랜드마크 문자열을 서버로 전송
                client_socket.sendall(pose_landmarks_str.encode())

            # 이미지 출력
            image = cv2.cvtColor(image, cv2.COLOR_RGB2BGR)
            mp_drawing.draw_landmarks(
                image, results.pose_landmarks, mp.solutions.pose.POSE_CONNECTIONS)
            cv2.imshow('MediaPipe Pose', image)

            # 키 입력 처리
            if cv2.waitKey(5) & 0xFF == ord('q'):
                break

        # 자원 해제
        cap.release()
        cv2.destroyAllWindows()

if __name__ == "__main__":
    send_pose_landmarks()

서버에 연결되었습니다. 127.0.0.1:6521
0.22081807255744934,0.2788868546485901,-0.6228510141372681;0.2468855381011963,0.24780195951461792,-0.5878170132637024;0.2578717768192291,0.25372862815856934,-0.5885637402534485;0.2678002417087555,0.2601122260093689,-0.589389443397522;0.21315324306488037,0.23193687200546265,-0.5626527667045593;0.20036908984184265,0.2263932228088379,-0.5620967149734497;0.18753568828105927,0.220944344997406,-0.5622295141220093;0.2756131887435913,0.28935128450393677,-0.305672287940979;0.1648813933134079,0.23465871810913086,-0.1816209852695465;0.22573038935661316,0.3388732671737671,-0.5149142146110535;0.1867786943912506,0.3194271922111511,-0.4813215136528015;0.3102422058582306,0.5292609930038452,-0.33896109461784363;0.04152678698301315,0.4305461049079895,0.1430230438709259;0.3947460949420929,0.8265402317047119,-0.48826056718826294;-0.043182697147130966,0.7140821814537048,0.1687183678150177;0.2671601474285126,0.9611427783966064,-0.7004320621490479;-0.016911376267671585,0.913311004